<a href="https://colab.research.google.com/github/shivamdhumal77/LLM_Projects/blob/main/llm_sound_1.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install torch
!pip install git+https://github.com/openai/whisper.git
!pip install parler-tts
!pip install transformers
!pip install langchain-community
!pip install soundfile
 # If you want to test audio playback functionality, though note it's not ideal for Colab.


  Cloning https://github.com/openai/whisper.git to /tmp/pip-req-build-sxihbkdq
  Running command git clone --filter=blob:none --quiet https://github.com/openai/whisper.git /tmp/pip-req-build-sxihbkdq
  Resolved https://github.com/openai/whisper.git to commit 517a43ecd132a2089d85f4ebc044728a71d49f6e
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 16.9 MB/s eta 0:00:00
  Created wheel for openai-whisper: filename=openai_whisper-20240930-py3-none-any.whl size=803669 sha256=566040a57574adfc8932a282db8565df6467a8f82ba59a9152a4807d38f60d31
  Stored in directory: /tmp/pip-ephem-wheel-cache-ksy7k2t7/wheels/1f/1d/98/9583695e6695a6ac0ad42d87511097dce5ba486647dbfecb0e
Successfully built openai-whisper
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 80.2/80.2 kB 3.7 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel

In [ ]:
pip install git+https://github.com/huggingface/parler-tts.git

  Cloning https://github.com/huggingface/parler-tts.git to /tmp/pip-req-build-9pi603vv
  Running command git clone --filter=blob:none --quiet https://github.com/huggingface/parler-tts.git /tmp/pip-req-build-9pi603vv
  Resolved https://github.com/huggingface/parler-tts.git to commit d108732cd57788ec86bc857d99a6cabd66663d68
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Cloning https://github.com/descriptinc/audiotools to /tmp/pip-install-r1wfgn9r/descript-audiotools_310bd2f31d59439f82ecd90c565106e6
  Running command git clone --filter=blob:none --quiet https://github.com/descriptinc/audiotools /tmp/pip-install-r1wfgn9r/descript-audiotools_310bd2f31d59439f82ecd90c565106e6
  Resolved https://github.com/descriptinc/audiotools to commit 348ebf2034ce24e2a91a553e3171cb00c0c71678
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.1/44.1 kB 3.6 MB/s eta 0:00:00
  Prep

In [ ]:
pip install colab-xterm

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.6/115.6 kB 6.1 MB/s eta 0:00:00


In [ ]:
%load_ext colabxterm

In [ ]:
# put this in the terminal and follow these steps
#curl https://ollama.ai/install.sh | sh
# ollama serve & ollama pull llama3.2
%xterm

Launching Xterm...

<IPython.core.display.Javascript object>

In [ ]:
%xterm

Launching Xterm...

<IPython.core.display.Javascript object>

In [ ]:
pip install ollama

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.4/76.4 kB 8.1 MB/s eta 0:00:00
  Attempting uninstall: httpx
    Found existing installation: httpx 0.28.1
    Uninstalling httpx-0.28.1:
      Successfully uninstalled httpx-0.28.1


In [ ]:
%xterm

Launching Xterm...

<IPython.core.display.Javascript object>

In [ ]:
%xterm

Launching Xterm...

<IPython.core.display.Javascript object>

In [ ]:
import whisper
import torch
from parler_tts import ParlerTTSForConditionalGeneration
from transformers import AutoTokenizer, set_seed
import numpy as np
from langchain_community.llms.ollama import Ollama
import soundfile as sf
from IPython.display import Audio

# Initialize Whisper model for transcription
whisper_model = whisper.load_model("tiny")  # Use 'tiny' for faster transcription

# Initialize ParlerTTS for speech synthesis
device = "cuda:0" if torch.cuda.is_available() else "cpu"
model_name = "parler-tts/parler-tts-mini-v1"  # Adjust this model name as needed
tts_model = ParlerTTSForConditionalGeneration.from_pretrained(model_name).to(device)
tokenizer = AutoTokenizer.from_pretrained(model_name)

# Initialize Ollama for text-based response generation
ollama = Ollama(model="llama3.2")

# Function for transcribing uploaded audio file using Whisper
def transcribe_from_audio(file_path):
    audio = whisper.load_audio(file_path)
    audio = whisper.pad_or_trim(audio)
    mel = whisper.log_mel_spectrogram(audio).to(device)

    options = whisper.DecodingOptions(fp16=False)
    result = whisper.decode(whisper_model, mel, options)
    return result.text

# Function for generating a response from Ollama
def generate_response(user_input):
    print(f"User: {user_input}")
    response = ollama(user_input)
    response_text = response.strip()  # Clean up the response
    print(f"Ollama: {response_text}")
    return response_text

# Function to synthesize speech using ParlerTTS
def synthesize_speech(text, voice_description):
    input_ids = tokenizer(voice_description, return_tensors="pt").input_ids.to(device)
    prompt_input_ids = tokenizer(text, return_tensors="pt").input_ids.to(device)
    generation = tts_model.generate(input_ids=input_ids, prompt_input_ids=prompt_input_ids)
    audio_arr = generation.cpu().numpy().squeeze()
    return audio_arr

# Function to play audio using Colab's native player
def play_audio(audio_array, sample_rate=22050):
    sf.write("synthesized_audio.wav", audio_array, sample_rate)  # Save audio to a .wav file
    return Audio("synthesized_audio.wav", autoplay=True)  # Return an Audio object for playback in Colab

# Main function for simulating the conversation
def conversation(file_path):
    voice_description = "A female speaker delivers a slightly expressive and animated speech with a moderate speed and pitch. The recording is of very high quality, with the speaker's voice sounding clear and very close up"

    # Step 1: Transcribe user input from the uploaded audio file
    user_input = transcribe_from_audio(file_path)

    # Step 2: Generate a response using Ollama
    response = generate_response(user_input)

    # Step 3: Synthesize response into speech
    audio = synthesize_speech(response, voice_description)

    # Step 4: Play synthesized speech
    return play_audio(audio)


# Upload an audio file manually in Colab, e.g., using this code snippet:
from google.colab import files
uploaded = files.upload()

# Choose the first uploaded file to use for transcription
file_path = list(uploaded.keys())[0]

# Run the conversation (transcription, response generation, and playback)
conversation(file_path)



/usr/local/lib/python3.10/dist-packages/torch_xla/__init__.py:253: UserWarning: `tensorflow` can conflict with `torch-xla`. Prefer `tensorflow-cpu` when using PyTorch/XLA. To silence this warning, `pip uninstall -y tensorflow && pip install tensorflow-cpu`. If you are in a notebook environment such as Colab or Kaggle, restart your notebook runtime afterwards.
  warnings.warn(


In [ ]:
!sudo apt-get install libportaudio2
!pip install sounddevice

Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
The following NEW packages will be installed:
  libportaudio2
0 upgraded, 1 newly installed, 0 to remove and 0 not upgraded.
Need to get 65.3 kB of archives.
After this operation, 223 kB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu jammy/universe amd64 libportaudio2 amd64 19.6.0-1.1 [65.3 kB]
Fetched 65.3 kB in 1s (128 kB/s)
debconf: unable to initialize frontend: Dialog
debconf: (No usable dialog-like program is installed, so the dialog based frontend cannot be used. at /usr/share/perl5/Debconf/FrontEnd/Dialog.pm line 78, <> line 1.)
debconf: falling back to frontend: Readline
debconf: unable to initialize frontend: Readline
debconf: (This frontend requires a controlling tty.)
debconf: falling back to frontend: Teletype
dpkg-preconfigure: unable to re-open stdin: 
Selecting previously unselected package libportaudio2:amd64.
(Reading database ... 119639 file

In [ ]:
import sounddevice as sd

print(sd.query_devices())
print(f"Default Input Device: {sd.default.device}")



Default Input Device: [-1, -1]


In [ ]:
pip install openai-whisper

In [ ]:
import whisper
from langchain_community.llms import Ollama
import torch
from parler_tts import ParlerTTSForConditionalGeneration
from transformers import AutoTokenizer
import soundfile as sf


In [ ]:


# Step 1: Transcribe the audio file with Whisper
whisper_model = whisper.load_model("base")  # Adjust model size as needed

# Path to your audio file
audio_file = "/content/#3.wav"
result = whisper_model.transcribe(audio_file)

# Extract transcribed text from the result
transcribed_text = result["text"]

# Step 2: Send the transcribed text to Ollama 3.2 for generating a response
ollama = Ollama(model="llama3.2")  # Assuming you are using the Ollama 3.2 model
response = ollama(transcribed_text)

# Print the response from Ollama
print(f"Response from Ollama: {response}")

# Step 3: Use the response to generate speech with ParlerTTS
device = "cuda:0" if torch.cuda.is_available() else "cpu"

# Load the ParlerTTS model and tokenizer
model_tts = ParlerTTSForConditionalGeneration.from_pretrained("parler-tts/parler-tts-mini-v1").to(device)
tokenizer = AutoTokenizer.from_pretrained("parler-tts/parler-tts-mini-v1")

# Description for TTS (Adjust based on your requirements)
description = "A female speaker delivers a slightly expressive and animated speech with a moderate speed and pitch. The recording is of very high quality, with the speaker's voice sounding clear and very close up."

# Tokenize the input: the response from Ollama is used as the prompt
input_ids = tokenizer(description, return_tensors="pt").input_ids.to(device)
prompt_input_ids = tokenizer(response, return_tensors="pt").input_ids.to(device)

# Generate speech
generation = model_tts.generate(input_ids=input_ids, prompt_input_ids=prompt_input_ids)
audio_arr = generation.cpu().numpy().squeeze()

# Save the generated speech as an audio file
sf.write("parler_tts_out.wav", audio_arr, model_tts.config.sampling_rate)

print("Speech synthesis complete. Audio saved as parler_tts_out.wav")
# it worked

/usr/local/lib/python3.10/dist-packages/whisper/__init__.py:150: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  checkpoint = torch.load(fp, map_location=device)
<ipython-inpu

Response from Ollama: It sounds like you're ready to explore your family history and understand where your fiery personality might have originated.

So, your father... What's his story? Was he known for being feisty or strong-willed? Did he have any notable conflicts or challenges in his life that might have shaped him into the person he is today?

Also, what do you mean by "I am my parents"? Is there something specific about their personalities, behaviors, or values that you inherited from them?


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/6.93k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/3.51G [00:00<?, ?B/s]

...

spiece.model:   0%|          | 0.00/792k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/2.42M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/2.54k [00:00<?, ?B/s]

The attention mask is not set and cannot be inferred from input because pad token is same as eos token. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.


Speech synthesis complete. Audio saved as parler_tts_out.wav


In [ ]:
from IPython.display import Audio

def play_audio(audio_path):
    return Audio(audio_path)

# Example usage: Specify the path to your saved .wav file
audio_file_path = "/content/parler_tts_out.wav"  # Update this path with your actual file path

# Call the function to play the audio
play_audio(audio_file_path)


In [ ]:


# Step 1: Transcribe the audio file with Whisper
whisper_model = whisper.load_model("base")  # Adjust model size as needed

# Path to your audio file
audio_file = "/content/#5.wav"
result = whisper_model.transcribe(audio_file)

# Extract transcribed text from the result
transcribed_text = result["text"]

# Step 2: Send the transcribed text to Ollama 3.2 for generating a response
ollama = Ollama(model="llama3.2")  # Assuming you are using the Ollama 3.2 model
response = ollama(transcribed_text)

# Print the response from Ollama
print(f"Response from Ollama: {response}")

# Step 3: Use the response to generate speech with ParlerTTS
device = "cuda:0" if torch.cuda.is_available() else "cpu"

# Load the ParlerTTS model and tokenizer
model_tts = ParlerTTSForConditionalGeneration.from_pretrained("parler-tts/parler-tts-mini-v1").to(device)
tokenizer = AutoTokenizer.from_pretrained("parler-tts/parler-tts-mini-v1")

# Description for TTS (Adjust based on your requirements)
description = "A female speaker delivers a slightly expressive and animated speech with a moderate speed and pitch. The recording is of very high quality, with the speaker's voice sounding clear and very close up."

# Tokenize the input: the response from Ollama is used as the prompt
input_ids = tokenizer(description, return_tensors="pt").input_ids.to(device)
prompt_input_ids = tokenizer(response, return_tensors="pt").input_ids.to(device)

# Generate speech
generation = model_tts.generate(input_ids=input_ids, prompt_input_ids=prompt_input_ids)
audio_arr = generation.cpu().numpy().squeeze()

# Save the generated speech as an audio file
sf.write("parler_tts_out.wav", audio_arr, model_tts.config.sampling_rate)

print("Speech synthesis complete. Audio saved as parler_tts_out.wav")
# it worked

/usr/local/lib/python3.10/dist-packages/whisper/__init__.py:150: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  checkpoint = torch.load(fp, map_location=device)


ConnectionError: HTTPConnectionPool(host='localhost', port=11434): Max retries exceeded with url: /api/generate (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x7c7513363100>: Failed to establish a new connection: [Errno 111] Connection refused'))

In [1]:
pip install -U kokoro-onnx

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 4.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 162.6/162.6 kB 10.5 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 82.5/82.5 kB 6.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.1/10.1 MB 43.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.3/13.3 MB 49.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 46.0/46.0 kB 3.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.7/1.7 MB 57.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 59.9/59.9 kB 4.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 86.8/86.8 kB 7.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 213.4/213.4 kB 11.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 564.9/564.9 kB 23.1 MB/s eta 0:00:00
  Created wheel for pylatexenc: filename=pylatexenc-2.10-py3-none-any.whl size=136816 s

In [2]:
!pip install gtts IPython langchain_openai

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 54.2/54.2 kB 6.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 61.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 75.6 MB/s eta 0:00:00


In [3]:
!apt-get -qq -y install espeak-ng > /dev/null 2>&1
!pip install -q phonemizer torch transformers scipy munch

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.2/48.2 kB 2.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 103.8/103.8 kB 6.2 MB/s eta 0:00:00


In [6]:
# Install necessary packages
!pip install gtts IPython langchain_openai

from langchain_openai import ChatOpenAI
from gtts import gTTS
from IPython.display import Audio
import os
import concurrent.futures
import sounddevice as sd
import numpy as np

# Initialize the ChatOpenAI instance
llm = ChatOpenAI(
    api_key="ollama",  # Required, even if unused
    base_url="https://sunny-gerri-finsocialdigitalsystem-d9b385fa.koyeb.app/v1",
    model="athene-v2"
)

class KokoroTTS:
    def __init__(self):
        self.CHUNK_SIZE = 150
        self.SAMPLE_RATE = 22050
        self.VOICE = "default"
        self.SPEED = 1.0
        self.SYSTEM_PROMPT = "You are an assistant."
        self.messages = []
        self.executor = concurrent.futures.ThreadPoolExecutor(max_workers=2)

    def phonemize(self, text):
        # Simplified phonemizer placeholder
        return text

    def generate_audio(self, text, voice, speed):
        # Generate TTS audio data using gTTS
        tts = gTTS(text, lang='en')
        tts.save("chunk.mp3")
        with open("chunk.mp3", "rb") as f:
            audio_data = np.frombuffer(f.read(), dtype=np.float32)
        return audio_data

    def create_and_play_response(self, prompt: str):
        # Generate text from the LLM
        response = llm.predict(prompt)

        # Stream and process the response
        buffer = ""
        futures = []
        curr_str = ""
        for chunk in response.split(". "):  # Simulate streaming response
            buffer += chunk + ". "
            curr_str += chunk + ". "

            if len(buffer) < self.CHUNK_SIZE:
                continue

            # Process chunk
            chunk_text = buffer.strip()
            buffer = ""

            # Convert chunk to audio
            ph = self.phonemize(chunk_text)
            futures.append(
                self.executor.submit(
                    self.generate_audio, ph, self.VOICE, self.SPEED
                )
            )

        # Handle remaining buffer
        if buffer:
            ph = self.phonemize(buffer.strip())
            futures.append(
                self.executor.submit(
                    self.generate_audio, ph, self.VOICE, self.SPEED
                )
            )

        # Play generated audio
        with sd.OutputStream(
            samplerate=self.SAMPLE_RATE, channels=1, dtype=np.float32
        ) as out_stream:
            for fut in futures:
                audio_data = fut.result()
                if len(audio_data) > 0:
                    out_stream.write(audio_data.reshape(-1, 1))

# Instantiate KokoroTTS
kokoro_tts = KokoroTTS()

# Take input from the user
user_prompt = input("Enter your prompt: ")

# Generate and play response
print("\nProcessing and Playing Response...")
kokoro_tts.create_and_play_response(user_prompt)


ModuleNotFoundError: No module named 'sounddevice'

In [5]:
# Install dependencies silently (if not already done)
!git lfs install
!git clone https://huggingface.co/hexgrad/Kokoro-82M
%cd Kokoro-82M
!apt-get -qq -y install espeak-ng > /dev/null 2>&1
!pip install -q phonemizer torch transformers scipy munch requests langchain-openai

# Import necessary modules
from models import build_model
from kokoro import generate
import torch
from langchain_openai import ChatOpenAI
from IPython.display import display, Audio

# Setup device
device = 'cuda' if torch.cuda.is_available() else 'cpu'

# Initialize Kokoro model and voicepack
def initialize_kokoro():
    model_path = 'kokoro-v0_19.pth'
    voice_name = [
        'af',  # Default voice (Bella & Sarah mix)
        'af_bella', 'af_sarah', 'am_adam', 'am_michael',
        'bf_emma', 'bf_isabella', 'bm_george', 'bm_lewis',
        'af_nicole', 'af_sky',
    ][0]

    print("Loading Kokoro model...")
    model = build_model(model_path, device)
    voicepack = torch.load(f'voices/{voice_name}.pt', weights_only=True).to(device)
    print(f"Loaded voice: {voice_name}")
    return model, voicepack, voice_name

# Main TTS generation function
def kokoro_tts_generate(model, voicepack, voice_name, text):
    try:
        # Generate audio and phonemes
        print("Generating audio...")
        audio, phonemes = generate(model, text, voicepack, lang=voice_name[0])
        display(Audio(data=audio, rate=24000, autoplay=True))
        print("Phonemes used:", phonemes)
    except Exception as e:
        print(f"Error in TTS generation: {str(e)}")

# Main conversational chatbot
def chatbot():
    # Step 1: Initialize Kokoro model and voicepack
    print("Initializing Kokoro...")
    model, voicepack, voice_name = initialize_kokoro()

    # Step 2: Initialize LangChain OpenAI model
    llm = ChatOpenAI(
        api_key="ollama",  # Required, even if unused
        base_url="https://sunny-gerri-finsocialdigitalsystem-d9b385fa.koyeb.app/v1",
        model="athene-v2"
    )

    # Step 3: Start chatbot loop
    print("Chatbot is ready. Type 'exit' to end the conversation.")
    while True:
        # Get user input
        user_text = input("You: ")
        if user_text.lower() in ["exit", "quit"]:
            print("Chatbot: Goodbye!")
            break

        # Generate response using ChatOpenAI
        print("Chatbot: Generating response...")
        try:
            response_text = llm.predict(user_text)
            print(f"Chatbot: {response_text}")

            # Generate and play response using Kokoro TTS
            kokoro_tts_generate(model, voicepack, voice_name, response_text)
        except Exception as e:
            print(f"Error in generating response: {str(e)}")

if __name__ == "__main__":
    chatbot()


NotImplementedError: A UTF-8 locale is required. Got ANSI_X3.4-1968